# Programming Exercise: Comparison of Regulations
Your task is to train an MLP for the classification of the iris data set using different regularization methods.
You can use the given libraries, but you can also use other libraries.
Set all seeds to 42.

In [ ]:
# Please enter your names
name = "Fabian Langer, Yannik Bretschneider"

In [ ]:
import os
import random
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
from sklearn.datasets import load_iris
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

SEED = 42
os.environ["PYTHONHASHSEED"] = str(SEED)
random.seed(SEED)
np.random.seed(SEED)
tf.random.set_seed(SEED)

#load data
iris = load_iris()
X = iris.data     
y = iris.target  

X = StandardScaler().fit_transform(X)

X_train, X_val, y_train, y_val = train_test_split(
    X, y, test_size=0.3, stratify=y, random_state=SEED
)

# MLP (2 pts)

First, implement an MLP with an input of 4, a hidden size of 16, and an output of 3 (a two-layer MLP).
For the first layer, use the ReLU function, and for the last layer, the softmax function.

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.regularizers import l2
from tensorflow.keras.callbacks import EarlyStopping

def create_mlp(regularization_type=None, rate=0.0, gamma=0.0):
    """
    Creates and compiles a two-layer MLP with optional regularization.
    Resets random seeds each time to ensure models start with identical weights
    for a fair comparison.

    Args:
        regularization_type (str, optional): 'dropout' or 'l2'. Defaults to None.
        rate (float, optional): Dropout rate if type is 'dropout'. Defaults to 0.0.
        gamma (float, optional): L2 regularization factor if type is 'l2'. Defaults to 0.0.

    Returns:
        tf.keras.Model: A compiled Keras Sequential model.
    """
    # Reset all seeds to ensure models initialize identically before training
    os.environ["PYTHONHASHSEED"] = str(SEED)
    random.seed(SEED)
    np.random.seed(SEED)
    tf.random.set_seed(SEED)

    model = Sequential()
    
    # Input layer and the first hidden layer (4 -> 16)
    # L2 regularization is applied via the kernel_regularizer argument
    model.add(Dense(16, 
                    input_shape=(X_train.shape[1],), 
                    activation='relu', 
                    kernel_regularizer=l2(gamma) if regularization_type == 'l2' else None))
    
    # Add a dropout layer if specified
    if regularization_type == 'dropout':
        model.add(Dropout(rate, seed=SEED))
        
    # Output layer (16 -> 3)
    model.add(Dense(3, activation='softmax'))
    
    # Compile the model
    model.compile(optimizer='adam',
                  loss='sparse_categorical_crossentropy', # Use sparse for integer labels
                  metrics=['accuracy'])
    
    return model

# Train MLP without any regularization (1 pt)

Train an MLP with the given train/validation split for 200 epochs with a batch size of 16.
Track the train loss, train accuracy, validation loss, and validation accuracy for each epoch. (e.g., in four arrays) 

In [ ]:
mlp_plain = create_mlp()

# Train the model and store its history
# verbose=0 is used to keep the notebook output clean
history_plain = mlp_plain.fit(
    X_train, y_train,
    epochs=200,
    batch_size=16,
    validation_data=(X_val, y_val),
    verbose=0
)

# Train an MLP with dropout (1 pts)

Train another MLP on the given train/validation split for 200 epochs with a batch size of 16 and dropout of 0.6.
Track the train loss, train accuracy, validation loss, and validation accuracy for each epoch. (e.g., in four arrays)

In [ ]:
# Create the MLP with dropout regularization
mlp_dropout = create_mlp(regularization_type='dropout', rate=0.6)

# Train the model and store its history
history_dropout = mlp_dropout.fit(
    X_train, y_train,
    epochs=200,
    batch_size=16,
    validation_data=(X_val, y_val),
    verbose=0
)

# Train an MLP with the L2 Regularization (1 pts)

Train another MLP on the given train/validation split for 200 epochs with a batch size of 16 and the L2 Regularization with gamma = 0.02.
Track the train loss, train accuracy, validation loss, and validation accuracy for each epoch. (e.g., in four arrays)

In [ ]:
mlp_l2 = create_mlp(regularization_type='l2', gamma=0.02)

# Train the model and store its history
history_l2 = mlp_l2.fit(
    X_train, y_train,
    epochs=200,
    batch_size=16,
    validation_data=(X_val, y_val),
    verbose=0
)

# Train an MLP with early stopping and a patience of 20 (1 pts)

Train another MLP on the given train/validation split for 200 epochs with a batch size of 16 and use early stopping with a patience of 20.
Track the train loss, train accuracy, validation loss, and validation accuracy for each epoch. (e.g., in four arrays) Here it can stop earlier.

In [ ]:
# Create the MLP for early stopping
mlp_early_stopping = create_mlp()

# Define the EarlyStopping callback
# It monitors the validation loss and stops if it doesn't improve for 20 epochs.
# restore_best_weights=True ensures the final model has the weights from its best epoch.
early_stopping_callback = EarlyStopping(
    monitor='val_loss',
    patience=20,
    restore_best_weights=True
)

# Train the model with the early stopping callback
history_early_stopping = mlp_early_stopping.fit(
    X_train, y_train,
    epochs=200,
    batch_size=16,
    validation_data=(X_val, y_val),
    callbacks=[early_stopping_callback],
    verbose=0
)

# Plot the training of all four MLPs (2 pts)

Create a plot for each MLP that shows its train loss, train accuracy, validation loss, and validation accuracy for each epoch. The plot for the MLP with early stopping can stop earlier.

In [ ]:
def plot_history(history, title):
    """
    Plots the training and validation loss and accuracy from a Keras history object.
    
    Args:
        history (tf.keras.callbacks.History): The history object returned by model.fit().
        title (str): The main title for the plot.
    """
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 6))
    fig.suptitle(title, fontsize=16)

    # Plot Loss
    ax1.plot(history.history['loss'], label='Train Loss')
    ax1.plot(history.history['val_loss'], label='Validation Loss')
    ax1.set_title('Model Loss')
    ax1.set_xlabel('Epoch')
    ax1.set_ylabel('Loss')
    ax1.legend(loc='upper right')
    ax1.grid(True)

    # Plot Accuracy
    ax2.plot(history.history['accuracy'], label='Train Accuracy')
    ax2.plot(history.history['val_accuracy'], label='Validation Accuracy')
    ax2.set_title('Model Accuracy')
    ax2.set_xlabel('Epoch')
    ax2.set_ylabel('Accuracy')
    ax2.legend(loc='lower right')
    ax2.grid(True)
    
    plt.show()

# Generate the plots for all four training scenarios
plot_history(history_plain, 'MLP without Regularization')
plot_history(history_dropout, 'MLP with Dropout (rate=0.6)')
plot_history(history_l2, 'MLP with L2 Regularization (gamma=0.02)')
plot_history(history_early_stopping, 'MLP with Early Stopping (patience=20)')